In [3]:
import json
import pandas as pd
from selenium import webdriver               # Autoscrolling the entire webpage and extracting the html in soup object
from selenium.webdriver.common.action_chains import ActionChains
from bs4 import BeautifulSoup
import time
import concurrent.futures
from selenium.webdriver.chrome.service import Service
import requests
from selenium import webdriver
import re

C:\Users\supri\anaconda3\lib\site-packages\requests\__init__.py:89: RequestsDependencyWarning: urllib3 (1.26.14) or chardet (5.1.0) doesn't match a supported version!
  warnings.warn("urllib3 ({}) or chardet ({}) doesn't match a supported "


We are sending the links of a collection to this fucntion and this fucntion scrapes the page to find the total number of nftid of that collection

In [14]:
def gettotals(url) :  
    response = requests.get(url)
    # Parse the HTML content with Beautiful Soup
    soup = BeautifulSoup(response.text, 'html.parser')

    json_script = soup.find_all('script', {'type': 'application/json'})

    json_string = json_script[2].contents[0]
    json_data = json.loads(json_string)

    body_tag = json_data['body']
    json_dict = json.loads(body_tag)
    return json_dict['supply']


This fucntion gets the url, sends it to gettotals , gets the total numner of nftids, makes a tuple of nftidlink, name, ids and send that back to the caller.

In [15]:
def makelinks(url,name):
    listlink=[]
    if type(gettotals(url))!=int:
        return [],[],[]
    totals=gettotals(url)
    
    id_list=list(range(1,totals))
    for i in range(1,totals):
        a=i
        new=str(a)
        final=url+"/"+new
        listlink.append(final)
    return listlink,[name]*totals,id_list
    
    

# This is the main fucntion which is gonna be used for the process, it will take the url fof the nftid, extract the rarityscore and rank from the json script and return in a tuple format. There are multiple try catch exceptions of when server error occurs or when json file is not found and we will maintain that list sideways to try later. 

In [16]:
def maketuples(url, name, i):
    try:
        response = requests.get(url, verify=False, timeout=10) # Set a timeout of 10 seconds
        # Parse the HTML content with Beautiful Soup
        soup = BeautifulSoup(response.text, 'html.parser')
        json_script = soup.find_all('script', {'type': 'application/json'})

        if ((len(json_script) < 4) or (json_script[3].contents) == 0):
            return (name, i, -1, -1)
        json_string = json_script[3].contents[0]
        json_data = json.loads(json_string)

        body_tag = json_data['body']
        json_dict = json.loads(body_tag)
        if 'rarityScore' in json_dict:
            rarity_score = json_dict['rarityScore']
        else:
            rarity_score = -1
        if 'rank' in json_dict:
            rank = json_dict['rank']
        else:
            rank = -1

        final_tup = (name, i, rarity_score, rank)
        return final_tup
    
    except Exception as e:
        print(f"Error occurred for {url}: {e}")
        return (name, i, -1, -1) # Return a tuple with default values to in

In [17]:
df=pd.read_csv('data.csv')

In [18]:
LISTF=[]
ignore_lis=[]


#here theread pool executor is used for multithreading for mutipe calls and the resutts are added to the final list 

In [28]:
a=time.time()
for i in range(len(df)):
    print(i)
    url=df.loc[i][1] #extracting every collection list one by one sing url anf scrolling using driver
    name=df.loc[i][0]
    urls,names,ides=makelinks(url,name)
    if len(urls)==0:
        ignore_lis.append((url,name,i))
        continue
    final_list=[]
    with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
        try:
            futures = [executor.submit(maketuples, url, name,ide) for url, name,ide in zip(urls, names,ides)]
            
        except Exception as e:
            continue
        final_list = [f.result() for f in futures]
        
    LISTF.extend(final_list)
b=time.time()
print(b-a)
    
    

1000


C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

...

C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'raritysniper.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\supri\anaconda3\lib\site-packages\urllib3\conn

SSLError: HTTPSConnectionPool(host='raritysniper.com', port=443): Max retries exceeded with url: /meta-island/2639 (Caused by SSLError(SSLError(1, '[SSL: SSLV3_ALERT_HANDSHAKE_FAILURE] sslv3 alert handshake failure (_ssl.c:1123)')))

In [ ]:
dfnew = pd.DataFrame(LISTF, columns=['Name','id','rarityscore', 'rank'])
#the file is stored in the proces

In [61]:
df.to_csv('final_data.csv', index=False)

In [30]:
df_ig=pd.DataFrame(ignore_lis,columns=['Url','id']) #when server error occurs we keep it in the ignore list and again call for it later
df_ig.to_csv('xxx.csv',index=False)

# here we are dealing with the ignore_lis where the server error has occured, we will be calling them again

In [12]:
final_list=[]
with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
    try:
        futures = [executor.submit(maketuples, url, name,ide) for url, name,ide in ignore_lis]
            
    except Exception as e:
        continue
    final_list = [f.result() for f in futures]
LISTF.extend(final_list)

Url   id
0         https://raritysniper.com/crypto-bulls  302
1  https://raritysniper.com/the-haughty-mummies  306

# There are some tuples where rank and rarityscore has been set null due to json error. we will be removing those rows and changing them to list of tuples to call them again using the makeone link function. This is how we deal on the anomalies and produce the final dataset.

In [60]:
rows = df[(df['rank'] == -1) & (df['rarityscore'] == -1)]
df = df[~((df['rank'] == -1) & (df['rarityscore'] == -1))]


In [37]:
rows

Name    id  rarityscore  rank  Url
4832   Crypto Coven  4833         -1.0  -1.0  NaN
5005   Crypto Coven  5006         -1.0  -1.0  NaN
5447   Crypto Coven  5448         -1.0  -1.0  NaN
5508   Crypto Coven  5509         -1.0  -1.0  NaN
5831   Crypto Coven  5832         -1.0  -1.0  NaN
...             ...   ...          ...   ...  ...
58649           EXO  9516         -1.0  -1.0  NaN
60824     LonelyPop  1603         -1.0  -1.0  NaN
61502     LonelyPop  2281         -1.0  -1.0  NaN
62021     LonelyPop  2800         -1.0  -1.0  NaN
62024     LonelyPop  2803         -1.0  -1.0  NaN

[379 rows x 5 columns]

In [38]:
def makeonelink(strr):
    newstr = 'https://raritysniper.com/' + strr
    return newstr

rows['Name'] = rows['Name'].apply(makeonelink)

<ipython-input-38-674fc90c894b>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rows['Name'] = rows['Name'].apply(makeonelink)


In [39]:
tuples = list(df.to_records(index=False))

In [ ]:
final_list=[]
with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
    try:
        futures = [executor.submit(maketuples, url, name,ide) for url, name,ide in tuples]
            
    except Exception as e:
        final_list = [f.result() for f in futures]

dffinalto_csv('df_final', index=False)